In [1]:
import calitp
from calitp.tables import tbl
from siuba import *

import pandas as pd
import numpy as np
import geopandas as gpd
import fiona

from ipyleaflet import Map, GeoJSON, projections, basemaps, GeoData, LayersControl, WidgetControl, GeoJSON
from ipywidgets import Text, HTML

# import shapely
# from shapely.geometry import LineString, MultiPoint
# from shapely.ops import split, substring

# import zlib
# import datetime as dt

/Users/edasmalchi/anaconda3/envs/pd1/lib/python3.9/site-packages/google/auth/_default.py:68: UserWarning: Your application has authenticated using end user credentials from Google Cloud SDK without a quota project. You might receive a "quota exceeded" or "API not enabled" error. We recommend you rerun `gcloud auth application-default login` and make sure a quota project is added. Or you can use service accounts instead. For more information about service accounts, see https://cloud.google.com/docs/authentication/
  warnings.warn(_CLOUD_SDK_CREDENTIALS_WARNING)


In [2]:
tbl.views.gtfs_schedule_fact_daily_feed_routes() >> head(3)

# Source: lazy query
# DB Conn: Engine(bigquery://cal-itp-data-infra/?maximum_bytes_billed=5000000000)
# Preview:
              feed_key            route_key        date calitp_extracted_at  \
0  7355377336956013324 -6224866760289025024  2021-08-25          2021-08-12   
1  7355377336956013324 -6224866760289025024  2021-08-24          2021-08-12   
2  7355377336956013324 -6224866760289025024  2021-09-05          2021-08-12   

  calitp_deleted_at  
0        2021-09-08  
1        2021-09-08  
2        2021-09-08  
# .. may have more rows

In [3]:
rail_routes = (tbl.views.gtfs_schedule_fact_daily_feed_routes()
               >> filter(_.date == '2021-10-6')
               >> inner_join(_, tbl.views.gtfs_schedule_dim_routes(), on='route_key')
               >> filter(_.route_type.isin(['0', '1', '2']))
               >> collect())

In [4]:
rail_routes.columns

Index(['feed_key', 'route_key', 'date', 'calitp_extracted_at_x',
       'calitp_deleted_at_x', 'agency_name', 'agency_timezone', 'agency_id',
       'route_continuous_drop_off', 'route_continuous_pickup', 'route_url',
       'agency_fare_url', 'agency_lang', 'route_short_name',
       'route_text_color', 'calitp_url_number', 'calitp_itp_id', 'route_desc',
       'calitp_extracted_at_y', 'route_type', 'route_color', 'agency_email',
       'agency_url', 'route_long_name', 'calitp_deleted_at_y', 'agency_phone',
       'route_sort_order', 'route_id'],
      dtype='object')

In [5]:
rail_trips = (tbl.gtfs_schedule.trips()
             >> filter(_.calitp_itp_id.isin(rail_routes.calitp_itp_id))
             >> collect()
             >> distinct(_.shape_id, _keep_all=True))

In [6]:
rail_trips

calitp_itp_id  calitp_url_number   route_id  \
0               273                  0        001   
1               273                  0        001   
2               273                  0        011   
3               273                  0        011   
4               273                  0        011   
...             ...                ...        ...   
4596            182                  0  256-13149   
4597            182                  0  251-13149   
4598            182                  0   81-13149   
4599            182                  0  251-13149   
4600            182                  0  165-13149   

                                   service_id  \
0                                           1   
1                                           1   
2                                           1   
3                                           1   
4                                           1   
...                                       ...   
4596     SEPT21-D95-1_Weekday-PASAAM1-0111100   
4597  SEPT21-D03CAR-1_Weekday-HOLENB1-0100000   
4598  SEPT21-D03CAR-1_Weekday-NIGHMS1-0111100   
4599  SEPT21-D03CAR-1_Weekday-NIGHMS1-0111100   
4600  SEPT21-D15CAR-1_Weekday-MULHOB1-0100000   

                                               trip_id        shape_id  \
0                                               968818           39712   
1                                               968899           39713   
2                                               969058           39714   
3                                               969074           39715   
4                                               969079           39716   
...                                                ...             ...   
4596     54003049-SEPT21-D95-1_Weekday-PASAAM1-0111100  2560086_SEPT21   
4597  54012509-SEPT21-D03CAR-1_Weekday-HOLENB1-0100000  2510180_SEPT21   
4598  54010936-SEPT21-D03CAR-1_Weekday-NIGHMS1-0111100   810313_SEPT21   
4599  54011229-SEPT21-D03CAR-1_Weekday-NIGHMS1-0111100  2510178_SEPT21   
4600  53846909-SEPT21-D15CAR-1_Weekday-MULHOB1-0100000  1650155_SEPT21   

                trip_headsign trip_short_name direction_id block_id  \
0          Watt I-80 Stationl            None            0     0105   
1                Sunrise Mall            None            1     1131   
2      Land Park/City College            None            0     6211   
3      Land Park/City College            None            0     1105   
4     Natomas/Club Center Dr.            None            1     1101   
...                       ...             ...          ...      ...   
4596                     None            None            0  2560801   
4597                     None            None            0  2512202   
4598                     None            None            1  2513002   
4599                     None            None            1  2512802   
4600                     None            None            0  1655602   

     wheelchair_accessible bikes_allowed calitp_extracted_at  
0                     None          None          2021-08-25  
1                     None          None          2021-08-25  
2                     None          None          2021-08-25  
3                     None          None          2021-08-25  
4                     None          None          2021-08-25  
...                    ...           ...                 ...  
4596                  None          None          2021-09-21  
4597                  None          None          2021-09-21  
4598                  None          None          2021-09-21  
4599                  None          None          2021-09-21  
4600                  None          None          2021-09-21  

[4601 rows x 13 columns]

In [7]:
rail_stop_times = (tbl.gtfs_schedule.stop_times()
                  >> filter(_.calitp_itp_id.isin(rail_trips.calitp_itp_id))
                  >> filter(_.trip_id.isin(rail_trips.trip_id))
                  >> collect()
                  >> distinct(_.stop_id, _keep_all=True))

In [9]:
rail_stop_times

calitp_itp_id  calitp_url_number                           trip_id  \
0                279                  0                            976843   
1                279                  0                            940483   
2                279                  0                            938041   
3                279                  0                            938143   
4                279                  0                            981128   
...              ...                ...                               ...   
36555            200                  0  SM:11029228-136-Blocks-Sunday-50   
36556            200                  0                        SC:3150537   
36557            200                  0                        AC:4221020   
36558            200                  0                        AC:2205080   
36559            200                  0                        AC:2612020   

      stop_id stop_sequence arrival_time departure_time  \
0        DUBL             0     11:09:00       11:09:00   
1        OAKL             0     18:25:00       18:25:00   
2        CONC             0     07:13:00       07:14:00   
3        RICH             0     14:52:00       14:52:00   
4        PITT             0     17:30:00       17:31:00   
...       ...           ...          ...            ...   
36555  341629            56     14:15:26       14:15:26   
36556   62891            56     17:13:23       17:13:23   
36557   50467            56     22:11:15       22:11:15   
36558   58338            56     17:35:36       17:35:36   
36559   54223            56     12:30:51       12:30:51   

                                         stop_headsign pickup_type  \
0                                                 None        None   
1                                                 None        None   
2                                                 None        None   
3                                                 None        None   
4                                                 None        None   
...                                                ...         ...   
36555                                             None           0   
36556                                             None           0   
36557                 14 WEST OAKLAND BART VIA 14TH ST           0   
36558  40 BAY FAIR BART VIA FOOTHILL BLVD BANCROFT AVE           0   
36559              28 SAN LEANDRO BART VIA ALVARADO ST           0   

      drop_off_type continuous_pickup continuous_drop_off shape_dist_traveled  \
0              None              None                None                 0.0   
1              None              None                None                 0.0   
2              None              None                None                 0.0   
3              None              None                None                 0.0   
4              None              None                None                 0.0   
...             ...               ...                 ...                 ...   
36555             0              None                None                None   
36556             0              None                None            21.36870   
36557             0              None                None         15224.70000   
36558             0              None                None         14826.59000   
36559             0              None                None         16413.98000   

      timepoint calitp_extracted_at  
0          None          2021-09-28  
1          None          2021-09-28  
2          None          2021-09-28  
3          None          2021-09-28  
4          None          2021-09-28  
...         ...                 ...  
36555         0          2021-10-17  
36556         0          2021-10-17  
36557         0          2021-10-17  
36558         0          2021-10-17  
36559         0          2021-10-17  

[36560 rows x 15 columns]

In [11]:
rail_stops = (tbl.gtfs_schedule.stops()
              >> filter(_.calitp_itp_id.isin(rail_stop_times.calitp_itp_id))
              >> filter(_.stop_id.isin(rail_stop_times.stop_id))
              >> collect())

BadRequest: 400 POST https://bigquery.googleapis.com/bigquery/v2/projects/cal-itp-data-infra/jobs?prettyPrint=false: The query is too large. The maximum standard SQL query length is 1024.00K characters, including comments and white space characters.

(job ID: e4b91e1e-43d4-4103-a3db-918e0193e86a)

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             

In [ ]:
rail_stops

[PRC 21064.3](https://leginfo.legislature.ca.gov/faces/codes_displaySection.xhtml?sectionNum=21064.3.&lawCode=PRC)
* _Major transit stop means a site containing any of the following:
(a) An existing rail or bus rapid transit station.
(b) A ferry terminal served by either a bus or rail transit service.
(c) The intersection of two or more major bus routes with a frequency of service interval of 15 minutes or less during the morning and afternoon peak commute periods._
    * "Intersection" may not be sufficiently well-defined for this analysis

[PRC 21060.2](https://leginfo.legislature.ca.gov/faces/codes_displaySection.xhtml?lawCode=PRC&sectionNum=21060.2.&highlight=true&keyword=bus%20rapid%20transit)
* _(a) “Bus rapid transit” means a public mass transit service provided by a public agency or by a public-private partnership that includes all of the following features:
(1) Full-time dedicated bus lanes or operation in a separate right-of-way dedicated for public transportation with a frequency of service interval of 15 minutes or less during the morning and afternoon peak commute periods.
(2) Transit signal priority.
(3) All-door boarding.
(4) Fare collection system that promotes efficiency.
(5) Defined stations._
    * Unlikely to determine if a service qualifies as BRT under this definition using GTFS alone